# chapter 6. Learning to Classify Text

# 6.1 Supervised Classification

## 6.1.6   Sequence Classification

In [3]:
# Example 6-5. Part of Speech Tagging with a Consecutive Classifier

import nltk

def pos_features(sentence, i, history):   # [1]
     features = {"suffix(1)": sentence[i][-1:],
                 "suffix(2)": sentence[i][-2:],
                 "suffix(3)": sentence[i][-3:]}
     if i == 0:
         features["prev-word"] = "<START>"
         features["prev-tag"] = "<START>"
     else:
         features["prev-word"] = sentence[i-1]
         features["prev-tag"] = history[i-1]
     return features

            
class ConsecutivePosTagger(nltk.TaggerI):  # [2]
    def __init__(self, train_sents):
        train_set = []
        for tagged_sent in train_sents:
            untagged_sent = nltk.tag.untag(tagged_sent)
            history = []
            for i, (word, tag) in enumerate(tagged_sent):
                featureset = pos_features(untagged_sent, i, history)
                train_set.append( (featureset, tag) )
                history.append(tag)
        self.classifier = nltk.NaiveBayesClassifier.train(train_set)

    def tag(self, sentence):
        history = []
        for i, word in enumerate(sentence):
            featureset = pos_features(sentence, i, history)
            tag = self.classifier.classify(featureset)
            history.append(tag)
        return zip(sentence, history)

In [8]:
from nltk.corpus import brown

tagged_sents = brown.tagged_sents(categories='news')
size = int(len(tagged_sents) * 0.1)
train_sents, test_sents = tagged_sents[size:], tagged_sents[:size]
tagger = ConsecutivePosTagger(train_sents)
print(tagger.evaluate(test_sents))

0.798052851182


## 6.1.7   Other Methods for Sequence Classification

현재까지의 접근 방식은 한번 품사를 결정하면, 다시 수정할수 없다는 점이다.

이 문제에 대한 해결책 2가지가 있다.


(1) transformational strategy 사용하기. 
    - Transformational joint classifier
    - 입력에 대해 label 을 처음 할당하고, 다음 관련된 입력들과의 불일치를 보이면 이전에 할당된 label을 반복적으로 개선하다.
    - 예 : Brill tagger -- chapter 5.6

(2) 품사의 가능한 모든 순서에 점수를 부여하고, 가장 높은 점수의 순서를 선택하기.
    - Hidden Markov Models
    - Maximum Entropy Markov Models
    - Linear-Chain Conditional Random Field Models
    - 각 알고리즘마다 태깅순서에 점수 부여하는 방식이 다르다.
    

# 6.2  Further Examples of Supervised Classification

## 6.2.1   Sentence Segmentation

Sentence segmentation -- a classification task for punctuation

1st step : 기존에 문장으로 분리된 데이타를 가져와서, feature를 뽑기 적당한 형태로 변환한다.

In [18]:

sents = nltk.corpus.treebank_raw.sents()
tokens = []
boundaries = set()
offset = 0

for sent in sents:
    tokens.extend(sent)
    offset += len(sent)
    boundaries.add(offset-1)
    print sent, len(sent)

[u'.', u'START'] 2
[u'Pierre', u'Vinken', u',', u'61', u'years', u'old', u',', u'will', u'join', u'the', u'board', u'as', u'a', u'nonexecutive', u'director', u'Nov', u'.', u'29', u'.'] 19
[u'Mr', u'.', u'Vinken', u'is', u'chairman', u'of', u'Elsevier', u'N', u'.', u'V', u'.,', u'the', u'Dutch', u'publishing', u'group', u'.'] 16
[u'.', u'START'] 2
[u'Rudolph', u'Agnew', u',', u'55', u'years', u'old', u'and', u'former', u'chairman', u'of', u'Consolidated', u'Gold', u'Fields', u'PLC', u',', u'was', u'named', u'a', u'nonexecutive', u'director', u'of', u'this', u'British', u'industrial', u'conglomerate', u'.'] 26
[u'.', u'START'] 2
[u'A', u'form', u'of', u'asbestos', u'once', u'used', u'to', u'make', u'Kent', u'cigarette', u'filters', u'has', u'caused', u'a', u'high', u'percentage', u'of', u'cancer', u'deaths', u'among', u'a', u'group', u'of', u'workers', u'exposed', u'to', u'it', u'more', u'than', u'30', u'years', u'ago', u',', u'researchers', u'reported', u'.'] 36
[u'The', u'asbestos', u'

**tokens** : 개별 문장의 token 들을 모두 더한 list

In [10]:
print tokens

[u'.', u'START', u'Pierre', u'Vinken', u',', u'61', u'years', u'old', u',', u'will', u'join', u'the', u'board', u'as', u'a', u'nonexecutive', u'director', u'Nov', u'.', u'29', u'.', u'Mr', u'.', u'Vinken', u'is', u'chairman', u'of', u'Elsevier', u'N', u'.', u'V', u'.,', u'the', u'Dutch', u'publishing', u'group', u'.', u'.', u'START', u'Rudolph', u'Agnew', u',', u'55', u'years', u'old', u'and', u'former', u'chairman', u'of', u'Consolidated', u'Gold', u'Fields', u'PLC', u',', u'was', u'named', u'a', u'nonexecutive', u'director', u'of', u'this', u'British', u'industrial', u'conglomerate', u'.', u'.', u'START', u'A', u'form', u'of', u'asbestos', u'once', u'used', u'to', u'make', u'Kent', u'cigarette', u'filters', u'has', u'caused', u'a', u'high', u'percentage', u'of', u'cancer', u'deaths', u'among', u'a', u'group', u'of', u'workers', u'exposed', u'to', u'it', u'more', u'than', u'30', u'years', u'ago', u',', u'researchers', u'reported', u'.', u'The', u'asbestos', u'fiber', u',', u'crocidoli

**boundaries** : 모든 문장경계토큰(sentence-boundary tokens)의 색인을 담고있는 set.

In [11]:
print boundaries

set([99783, 1, 90116, 16389, 40968, 81929, 24587, 16396, 73741, 8207, 32784, 93292, 20, 64158, 57366, 8221, 36869, 89832, 84656, 24611, 36, 53254, 38, 98345, 73771, 8236, 64178, 8238, 49201, 73785, 49210, 67344, 16445, 64, 66, 32835, 101750, 93021, 91489, 24649, 16459, 34146, 65615, 36618, 82001, 57426, 49235, 8276, 90197, 32855, 41050, 8285, 73824, 90128, 32868, 38246, 102, 16487, 65640, 98410, 82029, 24688, 49265, 41075, 16502, 32887, 97056, 92863, 52651, 65662, 8319, 24704, 57474, 58731, 134, 43713, 41097, 41099, 49292, 32911, 39619, 79214, 65686, 57495, 8346, 65200, 8348, 32930, 163, 24740, 41126, 57511, 49320, 73897, 16554, 96238, 45833, 65712, 41137, 57522, 16568, 99701, 90304, 98497, 82114, 8390, 199, 49352, 57545, 98475, 16587, 211, 24788, 65749, 32982, 75295, 32804, 76495, 41180, 81957, 57569, 49378, 50555, 228, 57382, 51921, 98537, 65770, 237, 8430, 87571, 94248, 33010, 6867, 80206, 73973, 57590, 90359, 54019, 8442, 21887, 86058, 96675, 258, 24836, 49413, 41004, 16650, 65803,

In [14]:
a = list(boundaries)

In [15]:
print sorted(a)

[1, 20, 36, 38, 64, 66, 102, 134, 163, 199, 211, 228, 237, 258, 286, 310, 344, 365, 387, 406, 429, 453, 489, 512, 558, 617, 637, 655, 671, 692, 705, 739, 763, 796, 811, 821, 823, 846, 891, 907, 934, 958, 976, 1013, 1048, 1077, 1092, 1117, 1142, 1153, 1192, 1213, 1235, 1273, 1275, 1312, 1332, 1348, 1350, 1378, 1398, 1400, 1424, 1431, 1448, 1463, 1479, 1481, 1505, 1529, 1552, 1570, 1601, 1624, 1626, 1656, 1679, 1702, 1716, 1718, 1751, 1755, 1773, 1791, 1832, 1863, 1892, 1897, 1926, 1943, 1962, 1993, 2009, 2032, 2051, 2065, 2103, 2125, 2148, 2166, 2168, 2196, 2231, 2272, 2299, 2320, 2341, 2368, 2380, 2382, 2411, 2440, 2492, 2513, 2529, 2585, 2599, 2620, 2659, 2712, 2739, 2769, 2782, 2812, 2838, 2861, 2863, 2903, 2946, 2997, 3040, 3096, 3125, 3134, 3148, 3177, 3182, 3183, 3184, 3211, 3245, 3288, 3299, 3326, 3365, 3390, 3392, 3438, 3472, 3474, 3505, 3539, 3582, 3613, 3618, 3619, 3620, 3635, 3656, 3680, 3701, 3723, 3754, 3778, 3797, 3824, 3846, 3867, 3893, 3925, 3944, 3959, 3989, 4020, 4037,

Next step : 구두점이 문장 경계를 지시하는지 결정하는데 사용할 테이타 feature 를 지정해야한다.

In [19]:
def punct_features(tokens, i):
    return {'next-word-capitalized': tokens[i+1][0].isupper(),
            'prev-word': tokens[i-1].lower(),
            'punct': tokens[i],
            'prev-word-is-one-char': len(tokens[i-1]) == 1}

상기 feature extractor를 기반으로, labeled featuresets 의 list 를 만들수있다.

모든 구두점 token을 선택하고, 이것들이 경계토큰인지 아닌지를 tagging 하여,  labeled featuresets 의 list 를 만든다.

In [21]:
featuresets = [(punct_features(tokens, i), (i in boundaries))
                for i in range(1, len(tokens)-1)
                if tokens[i] in '.?!']

In [25]:
print featuresets

[({'next-word-capitalized': False, 'prev-word': u'nov', 'prev-word-is-one-char': False, 'punct': u'.'}, False), ({'next-word-capitalized': True, 'prev-word': u'29', 'prev-word-is-one-char': False, 'punct': u'.'}, True), ({'next-word-capitalized': True, 'prev-word': u'mr', 'prev-word-is-one-char': False, 'punct': u'.'}, False), ({'next-word-capitalized': True, 'prev-word': u'n', 'prev-word-is-one-char': True, 'punct': u'.'}, False), ({'next-word-capitalized': False, 'prev-word': u'group', 'prev-word-is-one-char': False, 'punct': u'.'}, True), ({'next-word-capitalized': True, 'prev-word': u'.', 'prev-word-is-one-char': True, 'punct': u'.'}, False), ({'next-word-capitalized': False, 'prev-word': u'conglomerate', 'prev-word-is-one-char': False, 'punct': u'.'}, True), ({'next-word-capitalized': True, 'prev-word': u'.', 'prev-word-is-one-char': True, 'punct': u'.'}, False), ({'next-word-capitalized': True, 'prev-word': u'reported', 'prev-word-is-one-char': False, 'punct': u'.'}, True), ({'ne

In [33]:
for x in featuresets:
    print x

({'next-word-capitalized': False, 'prev-word': u'nov', 'prev-word-is-one-char': False, 'punct': u'.'}, False)
({'next-word-capitalized': True, 'prev-word': u'29', 'prev-word-is-one-char': False, 'punct': u'.'}, True)
({'next-word-capitalized': True, 'prev-word': u'mr', 'prev-word-is-one-char': False, 'punct': u'.'}, False)
({'next-word-capitalized': True, 'prev-word': u'n', 'prev-word-is-one-char': True, 'punct': u'.'}, False)
({'next-word-capitalized': False, 'prev-word': u'group', 'prev-word-is-one-char': False, 'punct': u'.'}, True)
({'next-word-capitalized': True, 'prev-word': u'.', 'prev-word-is-one-char': True, 'punct': u'.'}, False)
({'next-word-capitalized': False, 'prev-word': u'conglomerate', 'prev-word-is-one-char': False, 'punct': u'.'}, True)
({'next-word-capitalized': True, 'prev-word': u'.', 'prev-word-is-one-char': True, 'punct': u'.'}, False)
({'next-word-capitalized': True, 'prev-word': u'reported', 'prev-word-is-one-char': False, 'punct': u'.'}, True)
({'next-word-ca

In [29]:
punct_features(tokens, 1)

{'next-word-capitalized': True,
 'prev-word': u'.',
 'prev-word-is-one-char': True,
 'punct': u'START'}

In [30]:
punct_features(tokens,2)

{'next-word-capitalized': True,
 'prev-word': u'start',
 'prev-word-is-one-char': False,
 'punct': u'Pierre'}

In [31]:
punct_features(tokens,3)

{'next-word-capitalized': False,
 'prev-word': u'pierre',
 'prev-word-is-one-char': False,
 'punct': u'Vinken'}

featuresets 을 사용하여, punctuation classifier 를 훈련시키고 평가할수있다.

In [22]:
size = int(len(featuresets) * 0.1)
train_set, test_set = featuresets[size:], featuresets[:size]
classifier = nltk.NaiveBayesClassifier.train(train_set)
nltk.classify.accuracy(classifier, test_set)

0.936026936026936

In [24]:
# Example 6-6 Classification Based Sentence Segmenter

def segment_sentences(words):
    start = 0
    sents = []
    for i, word in enumerate(words):
        if word in '.?!' and classifier.classify(punct_features(words, i)) == True:
            sents.append(words[start:i+1])
            start = i+1
    if start < len(words):
        sents.append(words[start:])
    return sents

## 6.2.2 Identifying Dialogue Act Types

**Dialog act (화행)**  http://en.wikipedia.org/wiki/Dialog_act

- A dialog act is a specialized **speech act**. 


**Speech act**  http://ko.wikipedia.org/wiki/%EC%96%B8%EC%96%B4%ED%96%89%EC%9C%84

- 언어행위(言語行為, speech act, 화행, 언어를 통해 이루어지는 행위)

Recognizing the dialogue acts underlying the utterances in a dialogue can be an important first step in understanding the conversation.

**NPS Chat Corpus** 사용하자. 여기에는 모든 메세지가  "Statement," "Emotion," "ynQuestion", "Continuer" 와 같은 **dialogue act 15가지 type** 중 하나로 label 되어있다. 

이것을 이용하여, 새로운 메세지를 dialogue act types 중 하나로 인식할수있는 classifier를 만들자.

**1st step** : 기초 메세지 데이타를 추출한다. XML 주석으로 표시된 자료구조를 사용하기위해 xml_posts() 를 사용.

In [34]:
posts = nltk.corpus.nps_chat.xml_posts()[:10000]

**next step** : 메세지 포스트가 어떤 단어를 포함하고 있는지 검사할 **feature extractor** 정의하기.

In [35]:
def dialogue_act_features(post):
    features = {}
    for word in nltk.word_tokenize(post):
        features['contains(%s)' % word.lower()] = True
    return features

**final step** : 각 메세지 포스트에 feature extractor 를 적용하여, 훈련데이타와 테스트데이타를 만든다. 

그리고 새로운 **classifier** 를 만든다.

In [40]:
# post.get('class') --> 메세지 포스트 dialogue act type 을 구한다.
featuresets = [(dialogue_act_features(post.text), post.get('class'))  
                for post in posts]

size = int(len(featuresets) * 0.1)
train_set, test_set = featuresets[size:], featuresets[:size]

classifier = nltk.NaiveBayesClassifier.train(train_set)

print(nltk.classify.accuracy(classifier, test_set))

0.668


In [39]:
print len(featuresets)
# print featuresets

for x in featuresets:
    print x

10000
({'contains(im)': True, 'contains(now)': True, 'contains(this)': True, 'contains(left)': True, 'contains(name)': True, 'contains(with)': True, 'contains(gay)': True}, 'Statement')
({'contains(:)': True, 'contains(p)': True}, 'Emotion')
({'contains(part)': True}, 'System')
({'contains(hey)': True, 'contains(everyone)': True}, 'Greet')
({'contains(well)': True, 'contains(ah)': True}, 'Statement')
({'contains(:10-19-20suser7)': True, 'contains(nick)': True}, 'System')
({'contains(is)': True, 'contains(a)': True, 'contains(.)': True, 'contains(name)': True, 'contains(10-19-20suser7)': True, 'contains(gay)': True}, 'Accept')
({'contains(a)': True, 'contains(.action)': True, 'contains(10-19-20suser121)': True, 'contains(gives)': True, 'contains(clap)': True, 'contains(golf)': True, 'contains(.)': True}, 'System')
({'contains(:)': True, 'contains())': True}, 'Emotion')
({'contains(join)': True}, 'System')
({'contains(10-19-20suser59)': True, 'contains(hi)': True}, 'Greet')
({'contains(2

## 6.2.3   Recognizing Textual Entailment

entailment (함의) -- http://en.wikipedia.org/wiki/Entailment_(pragmatics)
    
implicature (함축)

http://www.nltk.org/api/nltk.classify.html#nltk.classify.rte_classify.RTEFeatureExtractor

In [41]:
# Example 6-7 "Recognizing Text Entailment" Feature Extractor. 
# The RTEFeatureExtractor class builds a bag of words for both the text and 
# the hypothesis after throwing away some stopwords, then calculates overlap and difference.

def rte_features(rtepair):
    extractor = nltk.RTEFeatureExtractor(rtepair)
    features = {}
    features['word_overlap'] = len(extractor.overlap('word'))
    features['word_hyp_extra'] = len(extractor.hyp_extra('word'))
    features['ne_overlap'] = len(extractor.overlap('ne'))
    features['ne_hyp_extra'] = len(extractor.hyp_extra('ne'))
    return features


In [42]:
rtepair = nltk.corpus.rte.pairs(['rte3_dev.xml'])[33]
extractor = nltk.RTEFeatureExtractor(rtepair)
print(extractor.text_words)

print(extractor.hyp_words)

print(extractor.overlap('word'))

print(extractor.overlap('ne'))

print(extractor.hyp_extra('word'))

set(['Russia', 'Organisation', 'Shanghai', 'Asia', 'four', 'at', 'operation', 'SCO', 'Iran', 'Soviet', 'Davudi', 'fight', 'China', 'association', 'fledgling', 'terrorism', 'was', 'that', 'republics', 'Co', 'representing', 'former', 'Parviz', 'central', 'meeting', 'together', 'binds'])
set(['member', 'SCO', 'China'])
set([])
set(['SCO', 'China'])
set(['member'])


# 6.4 Decision Trees

![figure6-4](images/fig6-4.png)

## 6.4.1   Entropy and Information Gain

In [20]:
import math

def entropy(labels):
    freqdist = nltk.FreqDist(labels)
    # print freqdist
    print dict(freqdist)
    probs = [freqdist.freq(l) for l in freqdist]
    print probs
    return -sum(p * math.log(p,2) for p in probs)

In [21]:
print(entropy(['male', 'male', 'male', 'male'])) 

print(entropy(['male', 'female', 'male', 'male']))

print(entropy(['female', 'male', 'female', 'male']))

print(entropy(['female', 'female', 'male', 'female']))

print(entropy(['female', 'female', 'female', 'female'])) 


{'male': 4}
[1.0]
-0.0
{'male': 3, 'female': 1}
[0.75, 0.25]
0.811278124459
{'male': 2, 'female': 2}
[0.5, 0.5]
1.0
{'male': 1, 'female': 3}
[0.25, 0.75]
0.811278124459
{'female': 4}
[1.0]
-0.0
